## CART using Python

### Import required Libraries

In [1]:
import pandas                   as     pd
import numpy                    as     np
import sklearn.datasets         as     datasets

from   sklearn                  import tree
from   sklearn.tree             import DecisionTreeClassifier
from   sklearn.externals.six    import StringIO  
from   IPython.display          import Image  
from   sklearn.tree             import export_graphviz 

from   sklearn.cross_validation import cross_val_score
from   sklearn.cross_validation import KFold

import pydotplus
import pydot

from   sklearn.model_selection  import  train_test_split

D:\Python\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


### Read data file

In [2]:
df              = pd.read_csv('D:/RRD/data/Loan_Default_Final.csv')
df.columns

Index(['bad_flag', 'tenure', 'margin_amount', 'financed_amount', 'exist',
       'cibil score', 'concurrent_loans', 'total_income', 'is_rented',
       'Gender', 'is_married', 'is_selfemployed ', 'age', 'monthly_expenses',
       'bank_savings'],
      dtype='object')

### Understand Data

In [3]:
df.columns        = ['bad_flag', 'tenure', 'margin_amount', 'financed_amount', 'exist', 'cibil score',\
                   'concurrent_loans', 'total_income', 'is_rented','Gender', 'is_married', \
                   'is_selfemployed', 'age', 'monthly_expenses','bank_savings']
feature_names   = df.columns
print(feature_names)
print(df.info())

Index(['bad_flag', 'tenure', 'margin_amount', 'financed_amount', 'exist',
       'cibil score', 'concurrent_loans', 'total_income', 'is_rented',
       'Gender', 'is_married', 'is_selfemployed', 'age', 'monthly_expenses',
       'bank_savings'],
      dtype='object')
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24783 entries, 0 to 24782
Data columns (total 15 columns):
bad_flag            24783 non-null int64
tenure              24783 non-null int64
margin_amount       24783 non-null int64
financed_amount     24783 non-null int64
exist               24783 non-null int64
cibil score         24783 non-null int64
concurrent_loans    24783 non-null int64
total_income        24783 non-null int64
is_rented           24783 non-null int64
Gender              24783 non-null int64
is_married          24783 non-null int64
is_selfemployed     24783 non-null int64
age                 24783 non-null int64
monthly_expenses    24783 non-null int64
bank_savings        24783 non-null int64
dtypes: 

In [4]:
print(df.head().T)

                       0        1        2        3        4
bad_flag               0        0        0        0        0
tenure                36       36       47       23       40
margin_amount        140     5079     1147     2741      811
financed_amount    82861   184262   131478   154791   209862
exist                  0        1        1        0        0
cibil score          731      698      709      704      689
concurrent_loans       0        3        1        2        3
total_income      994327  1842622  1314784  1547906  2518338
is_rented              0        0        0        0        1
Gender                 0        1        0        1        1
is_married             1        1        0        1        1
is_selfemployed        0        0        0        0        1
age                   28       41       53       45       46
monthly_expenses   41430    92131    32870    77395    83945
bank_savings      298298   368524   525913   309581   755501


### Observations

* There are no missing values and data looks OK
* All variables are numeric and the following variables need to be converted to Categorical variables:

| Sl No | Variable |
|-- | ----------------------- |
| 1 | bad_flag |
| 2 | exist |
| 3 | cibil score | 
| 4 | concurrent_loans |
| 5 | is_rented |
| 6 | Gender | 
| 7 | is_married |
| 8 | is_selfemployed |

In [5]:
categorical_var =  ['bad_flag','exist','cibil score','concurrent_loans','is_rented','Gender','is_married','is_selfemployed']
numerical_var   =  feature_names.drop(categorical_var)
#['tenure', 'margin_amount','financed_amount','total_income','age','monthly_expenses','bank_savings'] 
print(categorical_var)
print(numerical_var)

['bad_flag', 'exist', 'cibil score', 'concurrent_loans', 'is_rented', 'Gender', 'is_married', 'is_selfemployed']
Index(['tenure', 'margin_amount', 'financed_amount', 'total_income', 'age',
       'monthly_expenses', 'bank_savings'],
      dtype='object')


In [6]:
for i in range(len(categorical_var)):
    df[categorical_var[i]] = df[categorical_var[i]].astype('category') 

In [7]:
df.describe()

tenure  margin_amount  financed_amount  total_income  \
count  24783.000000   24783.000000     24783.000000  2.478300e+04   
mean      42.007667    1849.527821    143437.254529  1.577325e+06   
std        9.039933    1587.770308     45247.147140  5.129930e+05   
min        8.000000   -2135.000000     66938.000000  6.907760e+05   
25%       35.000000     781.000000    103197.000000  1.136604e+06   
50%       45.000000    1461.000000    143100.000000  1.549442e+06   
75%       47.000000    2467.500000    180728.000000  1.995998e+06   
max       96.000000   10947.000000    238084.000000  2.857002e+06   

                age  monthly_expenses  bank_savings  
count  24783.000000      24783.000000  2.478300e+04  
mean      41.573659      65667.796272  4.730027e+05  
std       10.983706      28933.367386  2.811703e+05  
min       23.000000      17710.000000  7.017100e+04  
25%       32.000000      43426.500000  2.379180e+05  
50%       42.000000      60339.000000  4.199160e+05  
75%       51.000000      83940.000000  6.532950e+05  
max       60.000000     164322.000000  1.428501e+06

In [8]:
df.describe(include = ['category'])

bad_flag  exist  cibil score  concurrent_loans  is_rented  Gender  \
count      24783  24783        24783             24783      24783   24783   
unique         2      2          201                 4          2       2   
top            0      0          781                 1          1       1   
freq       23263  20499          158              6255      12438   12460   

        is_married  is_selfemployed  
count        24783            24783  
unique           2                2  
top              0                0  
freq         12545            12422

### Create X, independent variable and y dependent variable

In [9]:
feature_names  =  feature_names.drop('bad_flag')
X              =  df.loc[:,feature_names] 
y              =  df.loc[:,'bad_flag']
label_names    =  y.unique()
print(X.shape)
print(y.shape)

(24783, 14)
(24783,)


### Check if the data set is balanced or not

In [10]:
y.value_counts().apply(lambda x: [x, ( x * 100) / df.shape[0]])

0    [23263, 93.86676350724287]
1     [1520, 6.133236492757132]
Name: bad_flag, dtype: object

Since class, 1 (Bad) customers form only 6% of the data set, we have a unbalanced data set.

### Split the data into training and test data set

In [11]:
seed      = 12234
test_size = 0.75
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = test_size, random_state = seed, stratify = y) 

Recursive partitioning is a fundamental tool in data mining. It helps us explore the structure of a set of data, while developing easy to visualize decision rules for predicting a categorical (classification tree) or continuous (regression tree) outcome.

CART Modeling via DecisionTreeClassifier

Classification and Regression Trees (as described by Brieman, Freidman, Olshenm and Stone) can be generated through the DecisionTreeClassifier package.

i) Grow the tree

For controlling tree growth, we set the following parameters:
* max_depth: The maximum depth of the tree.
* min_samples_split: The minimum number of samples required to split an internal node
* min_samples_leaf: min no of samples at a leaf node
* min_impurity_decrease : A node will be split if this split induces a decrease of the impurity greater than or equal to this value. 

In [12]:
feature_names = ['tenure', 'margin_amount', 'financed_amount', 'exist','cibil score', \
                 'concurrent_loans', 'total_income', 'is_rented','Gender', 'is_married',\
                 'is_selfemployed', 'age', 'monthly_expenses','bank_savings']
class_names   =  ['Good','Bad']

In [37]:
clf   =  DecisionTreeClassifier(    criterion = "gini", splitter = 'random', \
                                    min_samples_split = 2000, min_samples_leaf = 500, min_impurity_decrease = 2,\
                                    max_leaf_nodes = 500, max_depth= 6000)
clf.fit(X_train,y_train)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=6000,
            max_features=None, max_leaf_nodes=500, min_impurity_decrease=2,
            min_impurity_split=None, min_samples_leaf=500,
            min_samples_split=2000, min_weight_fraction_leaf=0.0,
            presort=False, random_state=None, splitter='random')

In [38]:
dot_data = StringIO()
export_graphviz(clf, out_file = dot_data, feature_names = feature_names, class_names = class_names, \
                rounded = True, proportion = False, precision = 2, filled = True)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  

In [39]:
(graph,) = pydot.graph_from_dot_file('tree.dot')
graph.write_png('tree.png')

In [40]:
Image('tree.png')

### Prune the tree

In [31]:
for ln in range(100,2000,200):
    dtree = tree.DecisionTreeClassifier(criterion = "gini", splitter = 'random', \
                                    max_leaf_nodes = ln, min_samples_leaf = 500,\
                                    max_depth= 5000)
    dtree.fit(X_train,y_train)
    dot_data = StringIO()
    export_graphviz(clf, out_file = dot_data, feature_names = feature_names, class_names = class_names, \
                rounded = True, proportion = False, precision = 2, filled = True)
    graph = pydotplus.graph_from_dot_data(dot_data.getvalue()) 
    (graph,) = pydot.graph_from_dot_file('tree.dot')
    graph.write_png('tree.png')
    Image('tree.png')

KeyboardInterrupt: 

http://dataaspirant.com/2017/02/01/decision-tree-algorithm-python-with-scikit-learn/